In [3]:
from urllib.request import urlopen
from urllib.error import HTTPError, URLError
from bs4 import BeautifulSoup
import time

In [4]:
def getSiteHTML(url):
    try:
        html = urlopen(url)
    except HTTPError as e:
        return
    except URLError as e:
        print('The server could not be found(((')
    else:
        return html

In [5]:
wildberries_urls = {'base': 'https://www.wildberries.ru',
                    'food': 'https://www.wildberries.ru/catalog/pitanie'}
wildberries_house_url = 'https://www.wildberries.ru/catalog/18993938/detail.aspx?targetUrl=GP'

wildberries_food_url = wildberries_urls['food']
html = getSiteHTML(wildberries_food_url)

In [6]:
bs = BeautifulSoup(html, 'html.parser')

In [7]:
bs.prettify()

'<!DOCTYPE html>\n<html class="adaptive" lang="ru" translate="no">\n <head>\n  <meta charset="utf-8"/>\n  <meta content="IE=7; IE=Edge" http-equiv="X-UA-Compatible"/>\n  <base href="https://www.wildberries.ru/"/>\n  <link href="wildberries://www.wildberries.ru/catalog/pitanie" rel="alternate"/>\n  <meta content="telephone=no" name="format-detection"/>\n  <meta content="no-referrer-when-downgrade" name="referrer"/>\n  <meta content="width=device-width, initial-scale=1" name="viewport"/>\n  <meta content="Wildberries" name="application-name">\n   <meta content="61b95d33285e2612" name="yandex-verification">\n    <meta content="guMau7oNvBifqUhZGuuGVtiGD0HkKe8v6uwYpvj2ZIg" name="google-site-verification">\n     <meta content="e08a4d66746555c8641fe953d12262c8" name="wmail-verification">\n      <link href="/manifestv2.txt" rel="manifest"/>\n      <link href="/opensearch.xml" rel="search" title="test" type="application/opensearchdescription+xml">\n       <link href="/favicon.ico" rel="icon" ty

In [8]:
catalog = bs.find('ul', {'class': 'menu-catalog__list-2'})

In [9]:
catalog.find_all('a')

[<a href="/catalog/produkty/vkusnye-podarki">Вкусные подарки</a>,
 <a href="/catalog/produkty-pitaniya/chay-kofe">Чай и кофе</a>,
 <a href="/catalog/pitanie/sladosti">Сладости и хлебобулочные изделия</a>,
 <a href="/catalog/pitanie/bakaleya">Бакалея</a>,
 <a href="/catalog/pitanie/detskoe-pitanie">Детское питание</a>,
 <a href="/catalog/produkty/dobavki-pishchevye">Добавки пищевые</a>,
 <a href="/catalog/pitanie/zdorovoe-pitanie">Здоровое питание</a>,
 <a href="/catalog/produkty/myasnaya-produktsiya">Мясная продукция</a>,
 <a href="/catalog/pitanie/chay-kofe/moloko-i-slivki">Молочные продукты и яйца</a>,
 <a href="/catalog/pitanie/napitki">Напитки</a>,
 <a href="/catalog/pitanie/sneki">Снеки</a>,
 <a href="/catalog/produkty/zamorozhennaya-produktsiya">Замороженная продукция</a>,
 <a href="/catalog/produkty/frukty">Фрукты и ягоды</a>,
 <a href="/catalog/produkty/ovoshchi">Овощи</a>]

In [10]:
category_urls = []
for link in catalog.find_all('a'):
    if 'href' in link.attrs:
        category_urls.append(str(link.attrs['href']))
category_urls

['/catalog/produkty/vkusnye-podarki',
 '/catalog/produkty-pitaniya/chay-kofe',
 '/catalog/pitanie/sladosti',
 '/catalog/pitanie/bakaleya',
 '/catalog/pitanie/detskoe-pitanie',
 '/catalog/produkty/dobavki-pishchevye',
 '/catalog/pitanie/zdorovoe-pitanie',
 '/catalog/produkty/myasnaya-produktsiya',
 '/catalog/pitanie/chay-kofe/moloko-i-slivki',
 '/catalog/pitanie/napitki',
 '/catalog/pitanie/sneki',
 '/catalog/produkty/zamorozhennaya-produktsiya',
 '/catalog/produkty/frukty',
 '/catalog/produkty/ovoshchi']

In [14]:
import aiohttp
import asyncio

base_url = wildberries_urls['base']
urls = [base_url + url for url in category_urls]

async def fetch_args(session, url):
    async with session.get(url) as response:
        html = await BeautifulSoup(response, 'html.parser')
        return html 


async def main():
    async with aiohttp.ClientSession() as session:
        # create a collection of coroutines(can be done with comprehension )
        fetch_coroutines = []
        for url in urls:
            fetch_coroutines.append(fetch_args(session, url))
        # waik up coroutines with gather
        data = await asyncio.gather(*fetch_coroutines)
        pprint(data)

        
asyncio.run(main())

RuntimeError: asyncio.run() cannot be called from a running event loop

In [9]:



food_categories_bs = []
for cat in category_urls:
    url = wildberries_urls['base'] + cat
    html = getSiteHTML(url)
    bs = BeautifulSoup(html, 'html.parser')
    food_categories_bs.append(bs)
    time.sleep(1) #Чтобы не забанило

In [10]:
food_categories_bs

[
 <!DOCTYPE html>
 
 <html class="adaptive" lang="ru" translate="no">
 <head>
 <meta charset="utf-8"/>
 <meta content="IE=7; IE=Edge" http-equiv="X-UA-Compatible"/>
 <base href="https://www.wildberries.ru/"/>
 <link href="wildberries://www.wildberries.ru/catalog/produkty/vkusnye-podarki" rel="alternate"/>
 <meta content="telephone=no" name="format-detection"/>
 <meta content="no-referrer-when-downgrade" name="referrer"/>
 <meta content="width=device-width, initial-scale=1" name="viewport"/>
 <meta content="Wildberries" name="application-name">
 <meta content="61b95d33285e2612" name="yandex-verification">
 <meta content="guMau7oNvBifqUhZGuuGVtiGD0HkKe8v6uwYpvj2ZIg" name="google-site-verification">
 <meta content="e08a4d66746555c8641fe953d12262c8" name="wmail-verification">
 <link href="/manifestv2.txt" rel="manifest"/>
 <link href="/opensearch.xml" rel="search" title="test" type="application/opensearchdescription+xml">
 <link href="/favicon.ico" rel="icon" type="image/vnd.microsoft.ico

In [13]:
products_list = food_categories_bs[0].find('div', {'class': 'product-card-list'})

In [15]:
import re
product_links = products_list.find_all('a', href=re.compile('\/catalog\/.*\/detail\.aspx\?targetUrl=GP'))
product_hrefs = [a.attrs['href'] for a in product_links]

In [16]:
product_hrefs

['/catalog/11689976/detail.aspx?targetUrl=GP',
 '/catalog/21403976/detail.aspx?targetUrl=GP',
 '/catalog/12304092/detail.aspx?targetUrl=GP',
 '/catalog/13707467/detail.aspx?targetUrl=GP',
 '/catalog/26747738/detail.aspx?targetUrl=GP',
 '/catalog/29036314/detail.aspx?targetUrl=GP',
 '/catalog/10337087/detail.aspx?targetUrl=GP',
 '/catalog/9542991/detail.aspx?targetUrl=GP',
 '/catalog/17393709/detail.aspx?targetUrl=GP',
 '/catalog/40732761/detail.aspx?targetUrl=GP',
 '/catalog/20864631/detail.aspx?targetUrl=GP',
 '/catalog/13371508/detail.aspx?targetUrl=GP',
 '/catalog/20864633/detail.aspx?targetUrl=GP',
 '/catalog/20864632/detail.aspx?targetUrl=GP',
 '/catalog/18947779/detail.aspx?targetUrl=GP',
 '/catalog/17393710/detail.aspx?targetUrl=GP',
 '/catalog/26389042/detail.aspx?targetUrl=GP',
 '/catalog/12151886/detail.aspx?targetUrl=GP',
 '/catalog/11285996/detail.aspx?targetUrl=GP',
 '/catalog/44679408/detail.aspx?targetUrl=GP',
 '/catalog/26389159/detail.aspx?targetUrl=GP',
 '/catalog/109

In [ ]:
f = open('pic','wb')
f.write(urlopen('http://images.wbstatic.net/c246x328/new/11680000/11689976-1.jpg').read())
f.close()

In [ ]:
import http.client

conn = http.client.HTTPSConnection("api.webscrapingapi.com")

conn.request("GET", "/v1?api_key=uVRZ8LWAucYxuCrcNy34F4BUfwSR2z7q&url=https%3A%2F%2Fapi.ipify.org%2F%3Fformat%3Djson&device=desktop&proxy_type=datacenter")

res = conn.getresponse()
data = res.read()

print(data.decode("utf-8"))

In [1]:
import requests

url = "https://api.webscrapingapi.com/v1"

params = {
  "api_key":"uVRZ8LWAucYxuCrcNy34F4BUfwSR2z7q",
  "url":"https://bing.com"
}

response = requests.request("GET", url, params=params)

print(response.text)

<!doctype html><html lang="en" dir="ltr"><head><meta name="theme-color" content="#4F4F4F" /><meta name="description" content="Bing helps you turn information into action, making it faster and easier to go from searching to doing." /><meta http-equiv="X-UA-Compatible" content="IE=edge" /><meta name="viewport" content="width=device-width, initial-scale=1.0" /><meta property="fb:app_id" content="570810223073062" /><meta property="og:type" content="website" /><meta property="og:title" content="Love At First Flight" /><meta property="og:image" content="https://www.bing.com/th?id=OHR.NorthernCaracara_EN-GB0825793460_tmb.jpg&amp;rf=" /><meta property="og:image:width" content="1366" /><meta property="og:image:height" content="768" /><meta property="og:url" content="https://www.bing.com/?form=HPFBBK&amp;ssd=20220405_2300&amp;mkt=en-GB" /><meta property="og:site_name" content="Bing" /><meta property="og:description" content="The crested caracara is no stranger to spring feve" /><title>Bing</titl